## Setting Up

In [1]:
import sys
sys.path.append('../src')

In [2]:
import os
import json, copy
import numpy as np
import cv2

In [3]:
valid_annot_data = None
file_path = '../data/processed/normalised_annot_data.json'
file_path

'../data/processed/normalised_annot_data.json'

## Loading the normalised annotations

In [4]:
try:
    with open(file_path, 'r') as f:
      valid_annot_data = json.load(f)
      print(f"[+] Successfully loaded normalised annotations from {file_path}")
except FileNotFoundError:
        print(f"Error: JSON file not found at {file_path}")
except json.JSONDecodeError as e:
        print(f"Error: Failed to parse JSON data from {file_path}: {e}")
except Exception as e:  # Catch other potential exceptions
        print(f"Error: An unexpected error occurred while reading JSON data: {e}")

[+] Successfully loaded normalised annotations from ../data/processed/normalised_annot_data.json


In [5]:
from utilities.utils import calc_bbox_coordinates
from utilities.utils import clear_files_in_directory
from utilities.utils import return_data_in_yolov8_format

In [6]:
modified_image_files_path = '../data/processed/images'
modified_label_files_path = '../data/processed/labels'
modified_image_files_path, modified_label_files_path

('../data/processed/images', '../data/processed/labels')

## Clearing the directories to remove garbage data(if any)

In [7]:
# First we make sure that both the folders are empty
clear_files_in_directory(f"{modified_image_files_path}/train")
clear_files_in_directory(f"{modified_image_files_path}/val")

clear_files_in_directory(f"{modified_label_files_path}/train")
clear_files_in_directory(f"{modified_label_files_path}/val")

Deleted file: ../data/processed/images/train/023906638.jpg
Deleted file: ../data/processed/images/train/097102913.jpg
Deleted file: ../data/processed/images/train/060732442.jpg
Deleted file: ../data/processed/images/train/099864788.jpg
Deleted file: ../data/processed/images/train/044019900.jpg
Deleted file: ../data/processed/images/train/090322362.jpg
Deleted file: ../data/processed/images/train/006383099.jpg
Deleted file: ../data/processed/images/train/042711245.jpg
Deleted file: ../data/processed/images/train/095943960.jpg
Deleted file: ../data/processed/images/train/062487410.jpg
Deleted file: ../data/processed/images/train/020642127.jpg
Deleted file: ../data/processed/images/train/008857834.jpg
Deleted file: ../data/processed/images/train/023868888.jpg
Deleted file: ../data/processed/images/train/028193688.jpg
Deleted file: ../data/processed/images/train/086728389.jpg
Deleted file: ../data/processed/images/train/040680480.jpg
Deleted file: ../data/processed/images/train/065201462.j

In [8]:
len(valid_annot_data)

17408

Divide into train and val set such that the each class have same distribution in both sets

In [9]:
train_set = []
val_set = []

In [10]:
activity_wise_information = dict() # This would contain data like {'activity_1': ['img1_name', 'img2_name']}
activity_wise_information

{}

Group into activity: [list of images with this activity]<br>
1-> First create an image: activity (hash table)

In [12]:
image_name_to_activity_hash = dict()
image_name_to_indx_hash = dict()
image_name_to_activity_hash, image_name_to_indx_hash

({}, {})

In [13]:
# Create an image_name->activity hash table
for i in range(len(valid_annot_data)):
    name = str(valid_annot_data[i]['name'])
    activity = str(valid_annot_data[i]['general_activity_name'])

    if activity == '[]': # Skip invalid categories
        print(f"[+] Invalid entry at: {i}")
        continue

    image_name_to_activity_hash[name] = activity

[+] Invalid entry at: 1771
[+] Invalid entry at: 2320
[+] Invalid entry at: 2396
[+] Invalid entry at: 3388
[+] Invalid entry at: 4120
[+] Invalid entry at: 4795
[+] Invalid entry at: 6406
[+] Invalid entry at: 6470
[+] Invalid entry at: 6577
[+] Invalid entry at: 6646
[+] Invalid entry at: 7446
[+] Invalid entry at: 7575
[+] Invalid entry at: 8236
[+] Invalid entry at: 8666
[+] Invalid entry at: 9098
[+] Invalid entry at: 9180
[+] Invalid entry at: 9349
[+] Invalid entry at: 9381
[+] Invalid entry at: 9586
[+] Invalid entry at: 9900
[+] Invalid entry at: 10044
[+] Invalid entry at: 10544
[+] Invalid entry at: 11395
[+] Invalid entry at: 12834
[+] Invalid entry at: 12902
[+] Invalid entry at: 13456
[+] Invalid entry at: 13606
[+] Invalid entry at: 13614
[+] Invalid entry at: 13732
[+] Invalid entry at: 14251
[+] Invalid entry at: 14257
[+] Invalid entry at: 14580
[+] Invalid entry at: 15035
[+] Invalid entry at: 15970
[+] Invalid entry at: 16083
[+] Invalid entry at: 16238
[+] Invalid 

In [14]:
# Create an image_name->indx hash table
for i in range(len(valid_annot_data)):
    name = str(valid_annot_data[i]['name'])
    indx = i

    image_name_to_indx_hash[name] = indx

In [15]:
image_name_to_indx_hash

{'090959539.jpg': 0,
 '079723958.jpg': 1,
 '023431911.jpg': 2,
 '046427237.jpg': 3,
 '059171697.jpg': 4,
 '079729537.jpg': 5,
 '073225928.jpg': 6,
 '093083286.jpg': 7,
 '050592625.jpg': 8,
 '048434290.jpg': 9,
 '072190957.jpg': 10,
 '077227561.jpg': 11,
 '040601254.jpg': 12,
 '002748519.jpg': 13,
 '040465542.jpg': 14,
 '076444073.jpg': 15,
 '019497520.jpg': 16,
 '033896993.jpg': 17,
 '006240232.jpg': 18,
 '086386676.jpg': 19,
 '019964802.jpg': 20,
 '060168661.jpg': 21,
 '020788587.jpg': 22,
 '033222776.jpg': 23,
 '028232635.jpg': 24,
 '078644482.jpg': 25,
 '030151454.jpg': 26,
 '035442495.jpg': 27,
 '090608706.jpg': 28,
 '060692228.jpg': 29,
 '094141118.jpg': 30,
 '077996220.jpg': 31,
 '075347561.jpg': 32,
 '049702365.jpg': 33,
 '068592922.jpg': 34,
 '046757036.jpg': 35,
 '003313346.jpg': 36,
 '038669149.jpg': 37,
 '050357007.jpg': 38,
 '071924520.jpg': 39,
 '082048758.jpg': 40,
 '051228474.jpg': 41,
 '018004990.jpg': 42,
 '083473795.jpg': 43,
 '008051656.jpg': 44,
 '012481767.jpg': 45

In [16]:
if len(activity_wise_information) == 0: # Pushing data into activity_wise_information
    for i in range(len(valid_annot_data)):
        if valid_annot_data[i]['name'] in image_name_to_activity_hash:
            activity = str(valid_annot_data[i]['general_activity_name'])

            if activity not in activity_wise_information:
                activity_wise_information[activity] = []
                (activity_wise_information[activity]).append(valid_annot_data[i]['name'])
            else:
                (activity_wise_information[activity]).append(valid_annot_data[i]['name'])

## Putting the data into train_set and val_set

<h4>We have splitted the data such that train:total = 0.6 and val:total = 0.4 for each class</h4>
<h4>Thus train_set and val_set have indentical distribution of data for each class(graphs for this are present in model_building_2.ipynb)</h4>

In [17]:
if len(train_set) == 0 and len(val_set) == 0:
    for activity in activity_wise_information.keys():
        # Iterate over each activity
        train_end = int(len(activity_wise_information[activity]) * 0.6)
        val_end = len(activity_wise_information[activity])
        
        for i in range(train_end):
            name = activity_wise_information[activity][i]
            # Find its index in valid annot data
            indx = image_name_to_indx_hash[name]
            train_set.append(copy.deepcopy(valid_annot_data[indx]))
        
        for i in range(train_end, val_end):
            name = activity_wise_information[activity][i]
            indx = image_name_to_indx_hash[name]
            val_set.append(copy.deepcopy(valid_annot_data[indx]))
else:
    print("[-] Train and Val set already created, aborting....")

Counting the average number of different joints per image

In [18]:
count_joints_train = {
    '0': 0,
    '1': 0,
    '2': 0,
    '3': 0,
    '4': 0,
    '5': 0,
    '6': 0,
    '7': 0,
    '8': 0,
    '9': 0,
    '10': 0,
    '11': 0,
    '12': 0,
    '13': 0,
    '14': 0,
    '15': 0,
}
count_joints_val = {
    '0': 0,
    '1': 0,
    '2': 0,
    '3': 0,
    '4': 0,
    '5': 0,
    '6': 0,
    '7': 0,
    '8': 0,
    '9': 0,
    '10': 0,
    '11': 0,
    '12': 0,
    '13': 0,
    '14': 0,
    '15': 0,
}

In [19]:
count_joints_train, count_joints_val

({'0': 0,
  '1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0,
  '13': 0,
  '14': 0,
  '15': 0},
 {'0': 0,
  '1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0,
  '13': 0,
  '14': 0,
  '15': 0})

In [20]:
jt_count_train, jt_count_val = False, False

In [21]:
# Finding the counts for training set
if not jt_count_train:
    for i in range(len(train_set)):
        for j in range(len(train_set[i]["personInfo"])):
            for k in range(len(train_set[i]["personInfo"][j]["x"])):
                if train_set[i]["personInfo"][j]["x"][k] > 0.001:
                    count_joints_train[str(k)] += 1
    jt_count_train = True
else:
    print('[-] Joint Count for train set already created, aborting')

In [22]:
# Finding the counts for validation set
if not jt_count_val:
    for i in range(len(val_set)):
        for j in range(len(val_set[i]["personInfo"])):
            for k in range(len(val_set[i]["personInfo"][j]["x"])):
                if val_set[i]["personInfo"][j]["x"][k] > 0.001:
                    count_joints_val[str(k)] += 1
    jt_count_val = True
else:
    print('[-] Joint Count for val set already created, aborting')

In [23]:
for key in count_joints_train.keys():
    count_joints_train[key] = (count_joints_train[key] * 1.0) / len(train_set)

In [24]:
for key in count_joints_val.keys():
    count_joints_val[key] = (count_joints_val[key] * 1.0) / len(val_set)

## Number of joints per image

In [25]:
count_joints_train

{'0': 1.1882081812944114,
 '1': 1.3964855002880738,
 '2': 1.621759170347609,
 '3': 1.6214710966007297,
 '4': 1.3964855002880738,
 '5': 1.1874399846360668,
 '6': 1.6153255233339734,
 '7': 1.6486460533896679,
 '8': 1.6478778567313233,
 '9': 1.6263683502976762,
 '10': 1.6429806030343768,
 '11': 1.647493758402151,
 '12': 1.6549836758210101,
 '13': 1.6537353562512003,
 '14': 1.6468215863260995,
 '15': 1.6383714230843096}

In [26]:
count_joints_val

{'0': 1.1987631238314396,
 '1': 1.396663310801093,
 '2': 1.6201639580037395,
 '3': 1.6205954264346325,
 '4': 1.4001150582482382,
 '5': 1.1990507694520351,
 '6': 1.6136919315403424,
 '7': 1.6463397094779233,
 '8': 1.6456205954264347,
 '9': 1.6230404142096937,
 '10': 1.6379979864806558,
 '11': 1.6457644182367324,
 '12': 1.6510858622177478,
 '13': 1.6522364447001294,
 '14': 1.644901481374946,
 '15': 1.6365597583776788}

In [1]:
# We can see that the train and val set also have identical distribution of data in terms of joints also

## Saving the training and validation set

In [27]:
modified_image_files_path, modified_label_files_path

('../data/processed/images', '../data/processed/labels')

In [28]:
image_height = 480
image_width = 640
image_height, image_width

(480, 640)

In [29]:
train_set_yolov8 = copy.deepcopy(train_set)
val_set_yolov8 = copy.deepcopy(val_set)
len(train_set_yolov8), len(val_set_yolov8)

(10414, 6953)

In [30]:
train_set_yolov8 = train_set_yolov8[:2400]
val_set_yolov8 = val_set_yolov8[:1200]

In [31]:
modified_image_files_path, modified_label_files_path

('../data/processed/images', '../data/processed/labels')

In [32]:
def save_train_data(train_set, read_image_files_path, modified_image_files_path, modified_label_files_path):
    for i in range(len(train_set)):
        image_name = train_set[i]["name"]
        image_path = read_image_files_path + f"/{image_name}"
        
        image = cv2.imread(image_path)
        data = return_data_in_yolov8_format(train_set, i, image_width, image_height) #only taking one-person per image---------

        image_path_new = modified_image_files_path + f"/train/{image_name}"
        annot_path_new = modified_label_files_path + f"/train/{image_name[:-4]}.txt"
        
        # Save the image
        try:
            # Check if image reading was successful
            if image is None:
                raise Exception("Failed to read image")

            # Save the image using cv2.imwrite()
            if cv2.imwrite(image_path_new, image):
                print(f"Image saved successfully to: {image_path_new}")
            else:
                raise Exception("Failed to save image")
        except Exception as e:
            print("Failed to save image:", e)
            break

        # Save the annotations
        try:
            with open(annot_path_new, 'w') as f:
                for item in data:
                    f.write(item + '\n')  # Write each item on a new line
                print(f"Data saved to {annot_path_new} successfully!")
        except Exception as e:
            print("Failed to save string:", e)
            break

In [34]:
len(train_set_yolov8), len(val_set_yolov8)

(2400, 1200)

In [35]:
save_train_data(train_set_yolov8, '../data/processed/images', '../data/processed/images', '../data/processed/labels')

Image saved successfully to: ../data/processed/images/train/090959539.jpg
Data saved to ../data/processed/labels/train/090959539.txt successfully!
Image saved successfully to: ../data/processed/images/train/050592625.jpg
Data saved to ../data/processed/labels/train/050592625.txt successfully!
Image saved successfully to: ../data/processed/images/train/077227561.jpg
Data saved to ../data/processed/labels/train/077227561.txt successfully!
Image saved successfully to: ../data/processed/images/train/094141118.jpg
Data saved to ../data/processed/labels/train/094141118.txt successfully!
Image saved successfully to: ../data/processed/images/train/027315962.jpg
Data saved to ../data/processed/labels/train/027315962.txt successfully!
Image saved successfully to: ../data/processed/images/train/024406345.jpg
Data saved to ../data/processed/labels/train/024406345.txt successfully!
Image saved successfully to: ../data/processed/images/train/097222971.jpg
Data saved to ../data/processed/labels/train

In [37]:
len(os.listdir('../data/processed/images/train')), len(os.listdir('../data/processed/labels/train'))

(2400, 2400)

In [38]:
save_train_data(train_set, '../data/processed/images', '../data/processed/images_pose', '../data/processed/labels_pose')

Image saved successfully to: ../data/processed/images_pose/train/090959539.jpg
Data saved to ../data/processed/labels_pose/train/090959539.txt successfully!
Image saved successfully to: ../data/processed/images_pose/train/050592625.jpg
Data saved to ../data/processed/labels_pose/train/050592625.txt successfully!
Image saved successfully to: ../data/processed/images_pose/train/077227561.jpg
Data saved to ../data/processed/labels_pose/train/077227561.txt successfully!
Image saved successfully to: ../data/processed/images_pose/train/094141118.jpg
Data saved to ../data/processed/labels_pose/train/094141118.txt successfully!
Image saved successfully to: ../data/processed/images_pose/train/027315962.jpg
Data saved to ../data/processed/labels_pose/train/027315962.txt successfully!
Image saved successfully to: ../data/processed/images_pose/train/024406345.jpg
Data saved to ../data/processed/labels_pose/train/024406345.txt successfully!
Image saved successfully to: ../data/processed/images_pose

In [39]:
len(os.listdir('../data/processed/images_pose/train')), len(os.listdir('../data/processed/labels_pose/train'))

(10414, 10414)

In [44]:
def save_val_data(val_set, read_image_files_path, modified_image_files_path, modified_label_files_path):
    for i in range(len(val_set)):
        image_name = val_set[i]["name"]
        image_path = read_image_files_path + f"/{image_name}"
        
        image = cv2.imread(image_path)
        data = return_data_in_yolov8_format(val_set, i, image_width, image_height) #only taking one-person per image

        image_path_new = modified_image_files_path + f"/val/{image_name}"
        annot_path_new = modified_label_files_path + f"/val/{image_name[:-4]}.txt"
        
        # Save the image
        cv2.imwrite(image_path_new, image)
        print(f"Image saved successfully to: {image_path_new}")

        # Save the annotations
        try:
            with open(annot_path_new, 'w') as f:
                for item in data:
                    f.write(item + '\n')  # Write each item on a new line
                print(f"Data saved to {annot_path_new} successfully!")
        except Exception as e:
            print("Failed to save string:", e)
            break

        print(f"String data saved successfully to: {annot_path_new}")

In [45]:
save_val_data(val_set_yolov8, '../data/processed/images', '../data/processed/images', '../data/processed/labels')

Image saved successfully to: ../data/processed/images/val/022177551.jpg
Data saved to ../data/processed/labels/val/022177551.txt successfully!
String data saved successfully to: ../data/processed/labels/val/022177551.txt
Image saved successfully to: ../data/processed/images/val/031216169.jpg
Data saved to ../data/processed/labels/val/031216169.txt successfully!
String data saved successfully to: ../data/processed/labels/val/031216169.txt
Image saved successfully to: ../data/processed/images/val/043621442.jpg
Data saved to ../data/processed/labels/val/043621442.txt successfully!
String data saved successfully to: ../data/processed/labels/val/043621442.txt
Image saved successfully to: ../data/processed/images/val/076576332.jpg
Data saved to ../data/processed/labels/val/076576332.txt successfully!
String data saved successfully to: ../data/processed/labels/val/076576332.txt
Image saved successfully to: ../data/processed/images/val/018626718.jpg
Data saved to ../data/processed/labels/val/0

In [46]:
len(os.listdir('../data/processed/images/val')), len(os.listdir('../data/processed/labels/val'))

(1200, 1200)

In [47]:
save_val_data(val_set, '../data/processed/images', '../data/processed/images_pose', '../data/processed/labels_pose')

Image saved successfully to: ../data/processed/images_pose/val/022177551.jpg
Data saved to ../data/processed/labels_pose/val/022177551.txt successfully!
String data saved successfully to: ../data/processed/labels_pose/val/022177551.txt
Image saved successfully to: ../data/processed/images_pose/val/031216169.jpg
Data saved to ../data/processed/labels_pose/val/031216169.txt successfully!
String data saved successfully to: ../data/processed/labels_pose/val/031216169.txt
Image saved successfully to: ../data/processed/images_pose/val/043621442.jpg
Data saved to ../data/processed/labels_pose/val/043621442.txt successfully!
String data saved successfully to: ../data/processed/labels_pose/val/043621442.txt
Image saved successfully to: ../data/processed/images_pose/val/076576332.jpg
Data saved to ../data/processed/labels_pose/val/076576332.txt successfully!
String data saved successfully to: ../data/processed/labels_pose/val/076576332.txt
Image saved successfully to: ../data/processed/images_po

In [48]:
len(os.listdir('../data/processed/images_pose/val')), len(os.listdir('../data/processed/labels_pose/val'))

(6953, 6953)